In [7]:
# Import dependencies
import pandas as pd
import altair as alt
import numpy as np
import geopandas as gpd

In [8]:
data = pd.read_csv("Geolocated Data - Sales & Prospect - 5.11.2023.csv", low_memory=False)

# Drop all features that are common between the prospect and sales dataframes
df = data.drop(['id','FullAddress', 'StreetName', 'JobStatus', 'SalesRepName1', 'SalesRepName2', 'Accuracy.Score', 'Accuracy.Type'], axis = 1)

# Prospect is defined by not having a contract date
prospect = df[df.ContractDate.isnull()]
sales = df.dropna(subset = ['ContractDate'])

# Drop unused features
sales = sales.drop(['DateAdded', 'Issued', 'Sat'], axis = 1)
prospect = prospect.drop(['GrossAmount', 'ContractDate','Source'], axis = 1)

# Drop rows with incomplete data
prospect = prospect.dropna()

# Remove zip codes that are not 5 digits (certain entries were throwing exceptions when converting to int)
prospect = prospect[prospect['Zip'].str.contains(r'^\d{5}$')]

sales = sales.where(sales['GrossAmount'] > 0, np.nan)

sales = sales.where(sales['State'] == 'NM', np.nan)
sales = sales.dropna()
# Adjust the type of various columns
sales = sales.astype({'productid':"str",
                      'City':'str',
                      'State':'str',
                      'Source':'str',
                      'SubSource':'str',
                      'Zip':'int'})

prospect = prospect.astype({'productid':'str',
                            'City':'str',
                            'State':'str',
                            'SubSource':'str'})
                            #'Zip':'int'})

# Set date field to use the datetime type
sales['ContractDate'] = pd.to_datetime(df.ContractDate)
#prospect['DateAdded'] = pd.to_datetime(df.DateAdded)

# Adjust the labels for sunroom products
sales = sales.replace({'SR-10':'Sunroom',
                    'SR-11':'Sunroom',
                    'SR-12':'Sunroom',
                    'SR-13':'Sunroom',
                    'SR-16':'Sunroom',
                    'SR-19':'Sunroom',
                    'SR-20':'Sunroom',
                    'SR-21':'Sunroom',
                    'SR-22':'Sunroom',
                    'SR-23':'Sunroom',
                    'SR-24':'Sunroom',
                    'SR-25':'Sunroom',
                    'SR-3':'Sunroom',
                    'SR-4':'Sunroom',
                    'SR-5':'Sunroom',
                    'SR-6':'Sunroom',
                    'SR-9':'Sunroom',
                    'Sun':'Sunroom',
                    'PC':'Patio cover',
                    'Win':'Window',
                    'Sid': 'Other',
                    'Stucco':'Other',
                    'Roof':'Other',
                    'SF':'Other',
                    'Deck':'Other'
})


In [13]:
alt.data_transformers.disable_max_rows()

interval = alt.selection_interval()

base = alt.Chart(sales).mark_point().encode(
    x = 'ContractDate:T',
    y = alt.Y('GrossAmount',axis = alt.Axis(title='Contract Price')),
    color = alt.Color('productid', legend=None)
)

chart = base.encode(
    x = alt.X('ContractDate:T', scale = alt.Scale(domain = interval)),
    tooltip = ['ContractDate', 'GrossAmount','productid', 'Zip']
).properties(
    width = 1000,
    height = 600,
    title = 'Historic Sales Record', 
).transform_filter(
    interval
)

hist = alt.Chart(sales).mark_bar().encode(
    y=alt.Y('count()', axis = alt.Axis(title=None)),
    x= alt.X('productid', axis = alt.Axis(title=None, labelAngle = -45)),
    color = 'productid',
    tooltip = ['count()', 'sum(GrossAmount)']
).properties(
    width=100,
    height=600,
    title = 'Projects sold'
).transform_filter(
    interval
)

view = alt.Chart(sales).mark_bar(size=1).encode(
    x = alt.X('ContractDate:T',
        axis = alt.Axis(title = 'Year')),
    y = alt.Y('sum(GrossAmount)', axis = alt.Axis(title = 'Total sales')),
    color = alt.Color('productid')
).add_params(
    interval
).properties(
    width = 1700,
    height = 150,
    title = "Click and drag to select a time frame. Double click to view full sales history."
)

#url = 'https://raw.githubusercontent.com/deldersveld/topojson/master/countries/us-states/NM-35-new-mexico-counties.json'
#data_map = alt.topo_feature(url, "cb_2015_new_mexico_county_20m")
data_map = gpd.read_file('Map Data\cb_2018_35_cousub_500k.shp')

map = alt.Chart(data_map).mark_geoshape(
    fill='lightgray',
    stroke='white'
).project('mercator').properties(
    width=500,
    height=600,
    title = 'Geographic location of sales'
)

geo = alt.Chart(sales).mark_circle().encode(
    longitude= 'Longitude:Q',
    latitude= 'Latitude:Q',
    size= alt.value(10),
    color = 'productid'
).transform_filter(
    interval
)

#(chart | legend) & view & hist & (base + geo)
(chart | hist | (map + geo)) & (view) 


alt.VConcatChart(...)

In [12]:
#data_map = gdfs["Map Data\cb_2018_35_cousub_500k.shp"].to_crs("epsg:4286")
data_map = gpd.read_file('Map Data\cb_2018_35_cousub_500k.shp')

map = alt.Chart(data_map).mark_geoshape(
    fill='lightgray',
    stroke='white'
).project('mercator').properties(
    width=500,
    height=600,
    title = 'Geographic location of sales'
)

(map)

alt.Chart(...)